PH-PLCd1 Data Files

FRAP was performed on an Olympus (Olympus Europa GmbH, Hamburg, Germany) FV-1000 system using a 60×/1.45 Oil UPlanSApo objective. A 128×128 pixel image was captured at 0.188 s intervals using a 488-nm laser line at 1% power and the pinhole set at 105 μm (back-projected pinhole diameter of approximately 250 μm). 
The images are taken of a C. elegans 1-cell embryo expressing a GFP fusion to the PH domain of Protein Lipase C delta 1 (PH-PLCd1).  This domain binds PIP2, a lipid enriched in the plasma membrane. 

Total Image Area
128x128 px

First Postbleach Frame
21

Resolution
Specified by file name in nm/pixel (“138” is 0.138 µm/px)

Edgelength
40 pixels

Date
20090504 (4 May 2009)




Your task in this problem is to extract the mean normalized fluorescence versus time from each of the TIFF stacks for the experimental repeats. 

In [274]:
import glob
import os

import numpy as np
import pandas as pd
import scipy.signal

# Image processing tools
import skimage
import skimage.io
import skimage.filters
import skimage.morphology

import bebi103

import bokeh
bokeh.io.output_notebook()

Loading BokehJS ...

In [275]:
# Load in TIFF stack
fname = '../data/goehring_FRAP_data/PH_138_A.tif'
ic = skimage.io.ImageCollection(fname, conserve_memory=False)[0]

# How long is it?
print('There are {0:d} frames.'.format(len(ic)))

There are 149 frames.


In [276]:
ip = 0.138 # micrometers

We want to segment the bleached area using the first postbleach frame, frame 21. Let's look at the frames right before and right after the FRAP event, frames 20 and 21.

In [4]:
def show_two_ims(im_1, im_2, titles=[None, None], interpixel_distances=[0.13, 0.13],
                 color_mapper=None):
    """Convenient function for showing two images side by side."""
    p_1 = bebi103.viz.imshow(im_1,
                             plot_height=300,
                             title=titles[0],
                             color_mapper=color_mapper,
                             interpixel_distance=interpixel_distances[0],
                             length_units='µm')
    p_2 = bebi103.viz.imshow(im_2,
                             plot_height=300,
                             title=titles[1],
                             color_mapper=color_mapper,
                             interpixel_distance=interpixel_distances[0],
                             length_units='µm')
    p_2.x_range = p_1.x_range
    p_2.y_range = p_1.y_range
    
    return bokeh.layouts.gridplot([p_1, p_2], ncols=2)

In [5]:
bokeh.io.show(show_two_ims(ic[19], ic[20], titles=['Frame 20', 'Frame 21'], interpixel_distances=[0.138, 0.138]))

Let's try direclty performing the Laplacian of Gaussian to denoise the image and find the edges of the square. First we need to convert the image to a float.

In [290]:
# Rename ic[20] to im for convenience
im = np.copy(ic[20])

# Convert image to float
im_float = skimage.img_as_float(im)

In [291]:
# Take a look at the image
p_1 = bebi103.viz.imshow(im_float,
                         plot_height=300,
                         title='im_float',
                         interpixel_distance=ip,
                         length_units='µm')

bokeh.io.show(p_1)

Now let's compute the LoG and display the results.

In [292]:
# Compute LoG
im_LoG = scipy.ndimage.filters.gaussian_laplace(im_float, 12.0)

# Check out results
bokeh.io.show(
    bebi103.viz.imshow(im_LoG,
                       color_mapper=bebi103.viz.mpl_cmap_to_color_mapper('bwr'),
                       interpixel_distance=ip,
                       length_units='µm',
                       colorbar=True))

In [293]:
# 3x3 square structuring element
selem = skimage.morphology.square(3)
    
# Do max filter and min filter
im_LoG_max = scipy.ndimage.filters.maximum_filter(im_LoG, footprint=selem)
im_LoG_min = scipy.ndimage.filters.minimum_filter(im_LoG, footprint=selem)

# Image of zero-crossings
im_edge = (  ((im_LoG >= 0) & (im_LoG_min < 0)) 
           | ((im_LoG <= 0) & (im_LoG_max > 0)))

# Show result
bokeh.io.show(show_two_ims(im_float,
                           im_edge,
                           titles=['original', 'edges']))

In [294]:
# Skeletonize edges
im_edge = skimage.morphology.skeletonize(im_edge)

# See result
bokeh.io.show(show_two_ims(im_float,
                           im_edge,
                           titles=['original', 'edges']))

In [295]:
# Fill holes
im_bw = scipy.ndimage.morphology.binary_fill_holes(im_edge)

# Remove small objectes that are not our square of interest
im_bw = skimage.morphology.remove_small_objects(im_bw, min_size=1000)

# Show result
bokeh.io.show(show_two_ims(im_float,
                           im_bw,
                           titles=['original', 'segmented']))

Our square is a little misshapen but let's go ahead and see if we can label it and start to extract information across frames.

In [296]:
# Label binary image; backward kwarg says value in im_bw to consider backgr.
im_labeled, n_labels = skimage.measure.label(
                            im_bw, background=0, return_num=True)

# Show number of labeled areas
print('Number of squares = ', n_labels)

# See result (one of the few times it's ok to use rainbow colormap!)
bokeh.io.show(
    bebi103.viz.imshow(im_labeled, 
                       interpixel_distance=ip,
                       length_units='µm'))

Number of squares =  1


In [297]:
# Get properties of this image
im_props = skimage.measure.regionprops(im_labeled, intensity_image=im)

In [299]:
data = [[prop.label, prop.area, prop.bbox, prop.centroid, prop.coords, prop.mean_intensity] for prop in im_props]
df = pd.DataFrame(data=data, columns=['label', 'area (sq µm)', 'bounding box coords', 'centroid', 'coords', 'mean intensity (a.u.)'])

# Take a look
df.head()

label  area (sq µm) bounding box coords  \
0      1          3178     (7, 12, 66, 75)   

                                centroid  \
0  (37.0824417872876, 41.92070484581498)   

                                              coords  mean intensity (a.u.)  
0  [[7, 52], [7, 53], [7, 54], [7, 55], [7, 56], ...              234.02297

We should either use the bounding box coords for our box for the rest of our mean intensity calculates or use the centroid, knowing that the edge length of the box should be 40 pixels, we can draw a box around the centroid where we measure the mean intensity.

In [289]:
# extracting intensity over time (this doesn't work cause our box will keep changing size
# and it wouldn't work before the frame with FRAP applied)


# for i, im in enumerate(ic):
#     print(i)
#     # Convert image to float
#     im_float = skimage.img_as_float(im)
#     # Compute LoG
#     im_LoG = scipy.ndimage.filters.gaussian_laplace(im_float, 12.0)

#     # 3x3 square structuring element
#     selem = skimage.morphology.square(3)

#     # Do max filter and min filter
#     im_LoG_max = scipy.ndimage.filters.maximum_filter(im_LoG, footprint=selem)
#     im_LoG_min = scipy.ndimage.filters.minimum_filter(im_LoG, footprint=selem)

#     # Image of zero-crossings
#     im_edge = (  ((im_LoG >= 0) & (im_LoG_min < 0)) 
#                | ((im_LoG <= 0) & (im_LoG_max > 0)))

#     # Skeletonize edges
#     im_edge = skimage.morphology.skeletonize(im_edge)
    
#     # Fill holes
#     im_bw = scipy.ndimage.morphology.binary_fill_holes(im_edge)

#     # Remove small objectes that are not our square of interest
#     im_bw = skimage.morphology.remove_small_objects(im_bw, min_size=1000)

#     # Label binary image; backward kwarg says value in im_bw to consider backgr.
#     im_labeled, n_labels = skimage.measure.label(
#                                 im_bw, background=0, return_num=True)
    
#     # Get properties of this image
#     im_props = skimage.measure.regionprops(im_labeled, intensity_image=im)

#     data = [[prop.label, prop.area, prop.mean_intensity] for prop in im_props]
#     df.loc[i, ['label', 'area (sq µm)', 'mean intensity (a.u.)'] = data

SyntaxError: invalid syntax (<ipython-input-289-da77e70fb5fc>, line 36)

Let's first try to remove any difference in background illumination.

In [9]:
# Rename ic[20] to im for convenience
im = np.copy(ic[20])

# Convert image to float
im_float = skimage.img_as_float(im)

In [14]:
# Filter the image with a strong Gaussian blur
im_bg = skimage.filters.gaussian(im_float, 60.0)

bokeh.io.show(show_two_ims(im_float, im_bg, titles=['original', 'background']))

We see that the upper left appears to have a stronger illumination in the upper left. Let's remove this change in background illumination.

In [15]:
# Subtract background
im_no_bg = im_float - im_bg

# Show images
bokeh.io.show(show_two_ims(im_float, im_no_bg, titles=['original', 'bg subtracted']))

Now let's try some filtering.

In [16]:
# Make slice object
zoom = np.s_[75:125, 75:125]

# Display zoom phase image
bokeh.io.show(
    bebi103.viz.imshow(im_no_bg[zoom], interpixel_distance=ip, length_units='µm'))

Let's try a median filter first.

In [187]:
# Use a median filter in a small square structuring element for median filter
selem = skimage.morphology.square(5)
im_filt = skimage.filters.rank.median(im, selem)

# Show results
bokeh.io.show(show_two_ims(im,
                           im_filt,
                           titles=['Original', 'Filtered']))

bokeh.io.show(show_two_ims(im[zoom],
                           im_filt[zoom],
                           titles=['Original', 'Filtered']))

In [109]:
# Use a median filter in a small square structuring element for median filter
selem = skimage.morphology.square(3)
im_float_filt = skimage.filters.rank.median(im_float, selem)

# Show results
bokeh.io.show(show_two_ims(im_float,
                           im_float_filt,
                           titles=['Original (float)', 'Filtered']))

bokeh.io.show(show_two_ims(im_float[zoom],
                           im_float_filt[zoom],
                           titles=['Original (float)', 'Filtered']))

In [105]:
# Use a median filter in a small square structuring element for median filter
selem = skimage.morphology.square(3)
im_filt = skimage.filters.rank.median(im_no_bg, selem)

# Show results
bokeh.io.show(show_two_ims(im_no_bg,
                           im_filt,
                           titles=['bg subtracted', 'Filtered']))

# Show results
bokeh.io.show(show_two_ims(im_no_bg[zoom],
                           im_filt[zoom],
                           titles=['bg subtracted', 'Filtered']))

For some reason when using the im_float to median filter, it comes out really weird?

Let's try the gaussian filter.

In [134]:
# Filter image
im_filt_gauss = skimage.filters.gaussian(im_float, 1.5)

# Show filtered image
bokeh.io.show(show_two_ims(im_float,
                           im_filt_gauss,
                           titles=['original', 'filtered']))

bokeh.io.show(show_two_ims(im_float[zoom],
                           im_filt_gauss[zoom],
                           titles=['original', 'filtered']))

In [116]:
# Filter image
im_float_no_bg =  skimage.img_as_float(im_no_bg)
im_filt_gauss = skimage.filters.gaussian(im_float_no_bg, 1.5)

# Show filtered image
# Show filtered image
bokeh.io.show(show_two_ims(im_float_no_bg,
                           im_filt_gauss,
                           titles=['original', 'filtered']))

bokeh.io.show(show_two_ims(im_float_no_bg[zoom],
                           im_filt_gauss[zoom],
                           titles=['bg subtracted', 'filtered']))

Let's also try the tv filter.

In [120]:
# Filter image
im_filt_tv = skimage.restoration.denoise_tv_chambolle(im_float, 0.005)

# Show filtered image
bokeh.io.show(show_two_ims(im_float,
                           im_filt_tv,
                           titles=['original', 'tv filtered']))

bokeh.io.show(show_two_ims(im_float[zoom],
                           im_filt_tv[zoom],
                           titles=['original', 'tv filtered']))

In [133]:
# Filter image
im_filt_tv = skimage.restoration.denoise_tv_chambolle(im_float, 0.01)

# Show filtered image
bokeh.io.show(show_two_ims(im_float,
                           im_filt_tv,
                           titles=['original', 'tv filtered']))

bokeh.io.show(show_two_ims(im_float[zoom],
                           im_filt_tv[zoom],
                           titles=['original', 'tv filtered']))

/Users/madelynw/anaconda3/lib/python3.7/site-packages/skimage/restoration/_denoise.py:226: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  g[slices_g] = np.diff(out, axis=ax)
/Users/madelynw/anaconda3/lib/python3.7/site-packages/skimage/restoration/_denoise.py:212: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  d[slices_d] += p[slices_p]


In [123]:
# Filter image
im_float_no_bg =  skimage.img_as_float(im_no_bg)
im_filt_tv = skimage.restoration.denoise_tv_chambolle(im_float_no_bg, 0.005)

# Show filtered image
bokeh.io.show(show_two_ims(im_float,
                           im_filt_tv,
                           titles=['original', 'tv filtered']))

bokeh.io.show(show_two_ims(im_float_no_bg[zoom],
                           im_filt_tv[zoom],
                           titles=['bg subtracted', 'tv filtered']))

Looks like filtering without subtracting the background is working better than filtering with subtracting the background in general?

Now I'm trying to plot histograms and threshold for each filter type.

In [136]:
def plot_hist(hist_bin, title, y_axis_type='linear'):
    """Make plot of image histogram."""
    p = bokeh.plotting.figure(plot_height=300,
                              plot_width=400,
                              y_axis_type=y_axis_type,
                              x_axis_label='intensity',
                              y_axis_label='count',
                              title=title)
    hist, bins = hist_bin
    p.line(bins, hist, line_width=2)

    return p

In [176]:
hist_bin = skimage.exposure.histogram(im)

# Display histogram with log scale
bokeh.io.show(plot_hist(hist_bin, 'original image', 'log'))

In [185]:
# Threshold image
thesh = 200
im_bw = im < 200

# Take a look
bokeh.io.show(show_two_ims(im_float,
                           im_bw,
                           titles=['original', 'thresholded']))

In [137]:
hist_bin = skimage.exposure.histogram(im_filt)

# Display histogram with log scale
bokeh.io.show(plot_hist(hist_bin, 'median filtered', 'log'))

In [138]:
hist_bin = skimage.exposure.histogram(im_filt_gauss)

# Display histogram with log scale
bokeh.io.show(plot_hist(hist_bin, 'gaussian filtered', 'log'))

In [139]:
hist_bin = skimage.exposure.histogram(im_filt_tv)

# Display histogram with log scale
bokeh.io.show(plot_hist(hist_bin, 'tv filtered', 'log'))

In [172]:
# Make the structuring element 25 pixel radius disk
selem = skimage.morphology.disk(30)

# Do the mean filter
im_mean = skimage.filters.rank.mean(im, selem)

# Threshhold based on mean filter
im_bw = im < 0.85 * im_mean

# Show the result
full = show_two_ims(im_float, im_bw, titles=['original', 'thresholded'])
zoomed = show_two_ims(im_float[zoom], im_bw[zoom])
bokeh.io.show(bokeh.layouts.column([full, zoomed]))

In [196]:
# Make the structuring element 25 pixel radius disk
selem = skimage.morphology.disk(30)

# Do the mean filter
im_mean = skimage.filters.rank.mean(im_filt, selem)

# Threshhold based on mean filter
im_bw = im_filt < 0.8 * im_mean

# Show the result
full = show_two_ims(im_filt, im_bw, titles=['median filtered', 'thresholded'])
zoomed = show_two_ims(im_filt[zoom], im_bw[zoom])
bokeh.io.show(bokeh.layouts.column([full, zoomed]))

In [162]:
# Make the structuring element 15 pixel radius disk
selem = skimage.morphology.disk(5)

# Do the mean filter
im_mean = skimage.filters.rank.mean(im_filt_gauss, selem)

# Threshhold based on mean filter
im_bw = im_filt_gauss < 0.85 * im_mean

# Show the result
full = show_two_ims(im_filt_gauss, im_bw, titles=['gaussian filtered', 'thresholded'])
zoomed = show_two_ims(im_filt_gauss[zoom], im_bw[zoom])
bokeh.io.show(bokeh.layouts.column([full, zoomed]))

In [156]:
# Make the structuring element 25 pixel radius disk
selem = skimage.morphology.disk(15)

# Do the mean filter
im_mean = skimage.filters.rank.mean(im_filt_tv, selem)

# Threshhold based on mean filter
im_bw = im_filt_tv < 0.85 * im_mean

# Show the result
full = show_two_ims(im_filt_tv, im_bw, titles=['tv filtered', 'thresholded'])
zoomed = show_two_ims(im_filt_tv[zoom], im_bw[zoom])
bokeh.io.show(bokeh.layouts.column([full, zoomed]))

In [190]:
# Compute number of pixels in binary image as a function of k
k = np.linspace(0.5, 1.0, 100)
n_pix = np.empty_like(k)
for i in range(len(k)):
    n_pix[i] = (im < k[i] * im_mean).sum()

# Plot the result
p = bokeh.plotting.figure(plot_height=300,
                          plot_width=500,
                          x_axis_label='k',
                          y_axis_label='number of pixels')
p.line(k, n_pix, line_width=2)
bokeh.io.show(p)

In [188]:
# Compute number of pixels in binary image as a function of k
k = np.linspace(0.5, 1.0, 100)
n_pix = np.empty_like(k)
for i in range(len(k)):
    n_pix[i] = (im_filt < k[i] * im_mean).sum()

# Plot the result
p = bokeh.plotting.figure(plot_height=300,
                          plot_width=500,
                          x_axis_label='k',
                          y_axis_label='number of pixels')
p.line(k, n_pix, line_width=2)
bokeh.io.show(p)

In [173]:
# Compute number of pixels in binary image as a function of k
k = np.linspace(0.5, 1.0, 100)
n_pix = np.empty_like(k)
for i in range(len(k)):
    n_pix[i] = (im_filt_gauss < k[i] * im_mean).sum()

# Plot the result
p = bokeh.plotting.figure(plot_height=300,
                          plot_width=500,
                          x_axis_label='k',
                          y_axis_label='number of pixels')
p.line(k, n_pix, line_width=2)
bokeh.io.show(p)

In [174]:
# Compute number of pixels in binary image as a function of k
k = np.linspace(0.5, 1.0, 100)
n_pix = np.empty_like(k)
for i in range(len(k)):
    n_pix[i] = (im_filt_tv < k[i] * im_mean).sum()

# Plot the result
p = bokeh.plotting.figure(plot_height=300,
                          plot_width=500,
                          x_axis_label='k',
                          y_axis_label='number of pixels')
p.line(k, n_pix, line_width=2)
bokeh.io.show(p)

In [197]:
# Compute rough second derivative
dn_pix_dk2 = np.diff(np.diff(n_pix))

# Find index of maximal second derivative
max_ind = np.argmax(dn_pix_dk2)

# Use this index to set k
k_opt = k[max_ind-2]

# Re-threshold with this k
im_bw = im < k_opt * im_mean

# Report the result
print('Optimal k = ', k_opt)

# Show images
full = show_two_ims(im_float, im_bw, titles=['original', 'thresholded'])
zoomed = show_two_ims(im_float[zoom], im_bw[zoom])
bokeh.io.show(bokeh.layouts.column([full, zoomed]))

Optimal k =  0.6464646464646464


In [201]:
# Remove all the small objects
im_bw = skimage.morphology.remove_small_objects(im_bw, min_size=25)

# Show images
full = show_two_ims(im_float, im_bw, titles=['original', 'thresholded'])
zoomed = show_two_ims(im_float[zoom], im_bw[zoom])
bokeh.io.show(bokeh.layouts.column([full, zoomed]))

In [207]:
# Structuring element is radius 2 disk
selem = skimage.morphology.disk(2)

# Dilate eroded image
im_bw_redilated = skimage.morphology.dilation(im_bw, selem)

# Look at the result
bokeh.io.show(show_two_ims(im_bw,
                           im_bw_redilated,
                           titles=['original bw', 'redilated']))

idea: use a square structuring element of edge length 40 and find the square with the lowest average intensity to detect our FRAP spot.